In [ ]:
from ngsolve import *
from ngsolve.webgui import Draw
from netgen.occ import *
from netgen.csg import *

def thermal_stress(delta_T, E, nu):
    cT = 2e-6
    return -E * cT * delta_T / (1 - 2 * nu)


def stress(strain, mu, lam):
    return 2 * mu * (strain) + lam * Trace(strain) * Id(3)


def mu(E, nu):
    return E / 2 / (1 + nu)


def lam(E, nu):
    return E * nu / ((1 + nu) * (1 - 2 * nu))

box1 = Box((0,0,0), (10,2.5,0.7))
box1.mat('part1')
box1.faces.Min(Y).maxh = 0.1
box2 = Box((0,0,0), (10,-1,3))
box2.mat('part2')
box2.faces.col = (0,0,1)

geo = OCCGeometry(Glue([box1,box2]))

mesh = Mesh(geo.GenerateMesh(maxh=0.5))

Draw(mesh)

# Mechanical parameters:
E_p1, nu_p1 = 2.10, 0.1
E_p2, nu_p2 = 80, 0.1

fes = VectorH1(mesh, order=3)

u, v  = fes.TnT()
gfu = GridFunction(fes)
dT1 = GridFunction(fes, definedon=mesh.Materials("part1"))
dT2 = GridFunction(fes, definedon=mesh.Materials("part2"))


a = BilinearForm(fes)
a += SymbolicEnergy(
    0.5 * InnerProduct(
        stress(Sym(Grad(u)), mu=mu(E_p1, nu_p1), lam=lam(E_p1, nu_p1)),
        Sym(Grad(u))
    ), definedon=mesh.Materials("part1")
)

a += SymbolicEnergy(
    0.5 * InnerProduct(
        stress(Sym(Grad(u)), mu=mu(E_p2, nu_p2), lam=lam(E_p2, nu_p2)),
        Sym(Grad(u))
    ), definedon=mesh.Materials("part2")
)

a += SymbolicEnergy(
        thermal_stress(dT1, E_p1, nu_p1) *
        u, definedon=mesh.Materials("part1")
)

a += SymbolicEnergy(
        thermal_stress(dT2, E_p2, nu_p2) *
        u, definedon=mesh.Materials("part2")
)

dT1.Set((-5e3*x, -5e3*y, -5e3*z))
dT2.Set((-1e3*x, -1e3*y, -1e3*z))


print('start')

solvers.NewtonMinimization(a, gfu, printing=False, inverse="sparsecholesky")

print('end')

WebGuiWidget(layout=Layout(height='50vh', width='100%'), value={'gui_settings': {}, 'ngsolve_version': '6.2.24…

start
